In [223]:
import torch
from torch.utils.data import Dataset, DataLoader
from torchvision import datasets
from torchvision.transforms import ToTensor, Compose, Lambda
import numpy as np
from time import perf_counter
import scipy.special
from numpy.linalg import norm

# To install pytorch on my system (MacBook and Anaconda python distribution), I used:
# conda install pytorch torchvision torchaudio -c pytorch
# search for directions for your system

# Refer to https://pytorch.org/tutorials/beginner/deep_learning_60min_blitz.html
# for PyTorch basics. Check out documentation in general.

In [224]:
# By default the images are returned as PIL images; transform them by converting first to 
# tensors with [0,1] entries then flattening them into vectors. Also, transform the integer
# class labels into one-hot encodings.

# See 
# https://pytorch.org/vision/stable/datasets.html#fashion-mnist
# https://pytorch.org/vision/stable/transforms.html#torchvision.transforms.ToTensor
# https://pytorch.org/vision/stable/transforms.html#torchvision.transforms.Compose

Flatten = Compose([ToTensor(), Lambda(lambda im : torch.flatten(im))])

OneHotEncode = Lambda( lambda y: 
    torch.zeros(10, dtype=torch.float).scatter_(0, torch.tensor(y), value=1))

training_data = datasets.FashionMNIST(
    root="data",
    train=True,
    download=True,
    transform=Flatten,
    target_transform=OneHotEncode
)

test_data = datasets.FashionMNIST(
    root="data",
    train=False,
    download=True,
    transform=Flatten,
    target_transform=OneHotEncode
)

In [229]:
# have 60000 training examples
# each training example is a (784 array, one-hot encoding of class 0-9)
training_data

training_data[0]
training_data[0][0].shape
training_data[0][1]

tensor([0., 0., 0., 0., 0., 0., 0., 0., 0., 1.])

In [230]:
# convert from the Pytorch dataset to numpy arrays using DataLoaders 
# with minibatch size equal to the full data size
train_loader = DataLoader(training_data, batch_size=len(training_data))
test_loader = DataLoader(test_data, batch_size=len(test_data))
trainX, trainy = next(iter(train_loader))
testX, testy = next(iter(test_loader))

# 60000 x 784 array of doubles; and 60000x 10 array of doubles
trainX, trainy = trainX.numpy(), trainy.numpy() 
testX, testy = testX.numpy(), testy.numpy()

In [231]:
class twolayerMLP:
    """Two layer MLP for logistic regression:
        first layer uses tanh activation
        second layer uses softmax activation
    
        Use debiased ADAM for optimization
    """
    
    def __init__(self, n0, n1, n2, regparam=1e-4):
        # n0 is the dimensionality of the input vectors
        # n1 is the number of hidden neurons
        # n2 is the number of output classes (labeled 0...(n2-1))
        # regparam is the weight decay parameter
        
        self.regparam = regparam
        
        self.W1 = np.random.uniform(-np.sqrt(6/(n0+n1)), np.sqrt(6/(n0+n1)), (n1, n0))
        self.W2 = np.random.uniform(-np.sqrt(6/(n1+n2)), np.sqrt(6/(n1+n2)), (n2, n1))
        self.b1 = np.zeros((n1, 1))
        self.b2 = np.zeros((n2,1))
        
        self.dW1 = np.zeros_like(self.W1)
        self.dW2 = np.zeros_like(self.W2)
        self.db1 = np.zeros_like(self.b1)
        self.db2 = np.zeros_like(self.b2)
        
        self.nuW1 = np.zeros_like(self.W1)
        self.nuW2 = np.zeros_like(self.W2)
        self.nub1 = np.zeros_like(self.b1)
        self.nub2 = np.zeros_like(self.b2)
        
        self.sW1 = np.zeros_like(self.W1)
        self.sW2 = np.zeros_like(self.W2)
        self.sb1 = np.zeros_like(self.b1)
        self.sb2 = np.zeros_like(self.b2)
        
        self.rW1 = np.zeros_like(self.W1)
        self.rW2 = np.zeros_like(self.W2)
        self.rb1 = np.zeros_like(self.b1)
        self.rb2 = np.zeros_like(self.b2)
        
        self.adamt = 0
        
    def sigma1(self, a):
        return np.tanh(a)
    
    def dsigma1(self, a):
        # derivative of tanh(x) = sech(x)^2 = 1/cosh(x)^2
        return 1/np.power(np.cosh(a), 2)
    
    def sigma2(self, a):
        # computes soft-max transform of each row of input a
        # use scipy's implementation instead of naive np.exp(v)/np.sum(np.exp(v))
        # because scipy's likely to be more numerically stable
        return scipy.special.softmax(a, axis=1)
        
    def forward(self, x, y):
        # computes the predicted class probability vector of each input row
        
        xt = x.T # so the columns are the datapoints
        yt = y.T # so the columns are the target class encodings
        self.a1 = self.W1 @ xt + self.b1
        self.o1 = self.sigma1(self.a1)
        self.a2 = self.W2 @ self.o1 + self.b2
        self.o2 = self.sigma2(self.a2)
  
        self.xt = xt
        self.yt = yt
        self.n = xt.shape[1] # number of samples in the training set

    def loss(self):
        # average CE-loss summed with l2 norms of parameters
        # see slide 16 of lecture 6 for the CE-loss 
        # https://www.cs.rpi.edu/~gittea/teaching/fall2021/files/Lecture6.pdf
        
        CEloss = -(1/self.n)*np.sum(self.yt*np.log(self.o2))
        Rloss = self.regparam * (norm(self.W1)**2 + norm(self.W2)**2 +
                                 norm(self.b1)**2 + norm(self.b2)**2)
        
        return CEloss + Rloss
    
    def valid_loss(self, x, y):
        # computes loss on a dataset without changing state of the class
        
        xt = x.T # so the columns are the datapoints
        yt = y.T # so the columns are the target class encodings
        a1 = self.W1 @ xt + self.b1
        o1 = self.sigma1(a1)
        a2 = self.W2 @ o1 + self.b2
        o2 = self.sigma2(a2)
  
        n = xt.shape[1] 
        
        CEloss = -(1/n)*np.sum(yt*np.log(o2))
        Rloss = self.regparam * (norm(self.W1)**2 + norm(self.W2)**2 +
                                 norm(self.b1)**2 + norm(self.b2)**2 )
        return CEloss + Rloss
    
    def dloss(self):
        # compute the gradient of the loss function w.r.t. 
        # the output of the final layer, o2
        # returns a matrix whose columns contain the gradients for each example
        
        return -(1/self.n) * self.yt / self.o2 
    
    def backward(self):
        # computes the derivative of the loss function w.r.t each parameter
        
        temp = self.dloss()
        
        ### compute the derivatives for the softmax parameters
        
        # useful fact: the jacobian of the softmax function satisfies 
        # J := J_o2(o1) = diag(o2) - o2 @ o2.T for a single column.
        # This is symmetric, so 
        # J @ g = o2 * g - (o2.T g) * o2. note also that J^T = J
        # Use the useful fact above and numpy broadcasting to compute the application of the 
        # jacobians over each sample in the batch efficiently
        Jtemp = self.o2 * temp - np.sum(self.o2 * temp, axis=0) * self.o2
        
        # We can conclude also that when o2 = softmax(W2 o1 + b2),
        # J_o2 (b2)^T temp = J @ temp
        # J_o2 (W2)^T temp = (J @ temp) * o1^T for a single column
        # Use these facts and numpy broadcasting to compute db2 and dW2 efficiently 
        self.db2 = np.sum(Jtemp, axis=1)[:,np.newaxis] + self.regparam * self.b2
        self.dW2 = Jtemp @ self.o1.T + self.regparam * self.W2
        
        ### compute the derivatives for the first layer of parameters
        
        temp = self.W2.T @ Jtemp 
        self.db1 = np.sum(self.dsigma1(self.a1) * temp, axis=1)[:, np.newaxis] + self.regparam * self.b1
        self.dW1 = (self.dsigma1(self.a1) * temp) @ self.xt.T + self.regparam * self.W1
        
    def subgrad_step(self, alpha=0.01):
        self.W1 = self.W1 - alpha * self.dW1
        self.W2 = self.W2 - alpha * self.dW2
        
        self.b1 = self.b1 - alpha * self.db1
        self.b2 = self.b2 - alpha * self.db2
        
    def adam_step(self, alpha=0.001, rho1 = 0.9, rho2 = 0.999, delta=1e-7):
        self.adamt += 1
        t = self.adamt
        
        # first moment estimates
        self.sW1 = rho1*self.sW1 + (1 - rho1)*self.dW1
        self.sW2 = rho1*self.sW2 + (1 - rho1)*self.dW2
        self.sb1 = rho1*self.sb1 + (1 - rho1)*self.db1
        self.sb2 = rho1*self.sb2 + (1 - rho1)*self.db2
        
        # debias the first moments
        sW1hat = self.sW1/(1 - rho1**t)
        sW2hat = self.sW2/(1 - rho1**t)
        sb1hat = self.sb1/(1 - rho1**t)
        sb2hat = self.sb2/(1 - rho1**t)
        
        # second moment estimates
        self.rW1 = rho2*self.rW1 + (1 - rho2)*(self.dW1 * self.dW1)
        self.rW2 = rho2*self.rW2 + (1 - rho2)*(self.dW2 * self.dW2)
        self.rb1 = rho2*self.rb1 + (1 - rho2)*(self.db1 * self.db1)
        self.rb2 = rho2*self.rb2 + (1 - rho2)*(self.db2 * self.db2)
        
        # debias the second moments
        rW1hat = self.rW1/(1 - rho2**t)
        rW2hat = self.rW2/(1 - rho2**t)
        rb1hat = self.rb1/(1 - rho2**t)
        rb2hat = self.rb2/(1 - rho2**t)
        
        self.W1 -= alpha * sW1hat/(np.sqrt(rW1hat) + delta)
        self.W2 -= alpha * sW2hat/(np.sqrt(rW2hat) + delta)
        self.b1 -= alpha * sb1hat/(np.sqrt(rb1hat) + delta)
        self.b2 -= alpha * sb2hat/(np.sqrt(rb2hat) + delta)
        
        

In [232]:
ntrain = len(trainX)
minibatch_indices = np.random.permutation(ntrain)
numsplits = ntrain//6000 # take batches of size 6000
numepochs = 100
nhidden = 400
regparam=1e-4

nn = twolayerMLP(784, nhidden, 10, regparam)

In [ ]:
for e in range(numepochs):
    print("Current training/validation loss [%d/%d]: %.2f, %.2f" % (e+1, numepochs, nn.valid_loss(trainX, trainy), nn.valid_loss(testX, testy)))
    minibatches = np.split(np.random.permutation(ntrain), numsplits)
    start_time = perf_counter()
    for indices in minibatches:
        Xbatch = trainX[indices, :]
        ybatch = trainy[indices, :]
        nn.forward(Xbatch, ybatch)
        nn.backward()
        nn.adam_step(alpha=1e-4)   
    end_time = perf_counter()
    accuracy = np.sum(np.argsort(nn.o2, axis=0)[9,:] == np.argsort(nn.yt, axis=0)[9,:])/nn.xt.shape[1]
    print("Current accuracy on training set: %.2f" % accuracy)
    print(" forward & backward pass took: %.2f (s)" % (end_time - start_time))  

Current training/validation loss [1/100]: 11.11, 9.31
Current accuracy on training set: 0.40
 forward & backward pass took: 3.27 (s)
Current training/validation loss [2/100]: 10.78, 8.99
Current accuracy on training set: 0.53
 forward & backward pass took: 3.23 (s)
Current training/validation loss [3/100]: 10.66, 8.86
Current accuracy on training set: 0.58
 forward & backward pass took: 3.13 (s)
Current training/validation loss [4/100]: 10.61, 8.81
Current accuracy on training set: 0.63
 forward & backward pass took: 3.26 (s)
Current training/validation loss [5/100]: 10.57, 8.77
Current accuracy on training set: 0.64
 forward & backward pass took: 3.30 (s)
Current training/validation loss [6/100]: 10.52, 8.72
Current accuracy on training set: 0.67
 forward & backward pass took: 3.13 (s)
Current training/validation loss [7/100]: 10.47, 8.68
Current accuracy on training set: 0.68
 forward & backward pass took: 3.25 (s)
Current training/validation loss [8/100]: 10.44, 8.64
Current accurac